# NCI with a Jupyter notebook #
_(Peter Reinhardt, Paris 2020)_

We approach the NCI with the simplest possible molecule, H$_2$ in a minimal basis. The orbital is a Slater function $N_a e^{-a r}$ with $a=1$, and thus $N=\sqrt{a^3/\pi}$.

In the notebook, we 
1. define an atomic orbital in 3D space, centered  at (R,0,0)
2. define a molecular orbital for H$_2$. The norm of the orbital can be approximated by a Gaussian function $a\, e^{-b R^2} + c\, e^{-d R^2}$
3. calculate grad rho / rho^(4/3) on the line going through the two atoms
4. upon varying R, we observe the evolution of this index

**The notebook is not complete - please fill in the missing parts !!**

In [1]:
def atomic_orb(x,y,z,R):
    import math
    from math import exp 
    from math import sqrt
    from math import pi
    
    r=math.sqrt((x-R)*(x-R)+y*y+z*z)
    val=math.sqrt(1./math.pi)*math.exp(-r) 
    return val

In [2]:
def grad_atomic_orb(x,y,z,R):
    import math
    from math import exp 
    from math import sqrt
    from math import pi
    
    denom=math.sqrt((x-R)*(x-R)+y*y+z*z)
    if (abs(denom) > 1.e-8):
        gradx=-atomic_orb(x,y,z,R)*(x-R)/denom
        grady=-atomic_orb(x,y,z,R)*y/denom
        gradz=-atomic_orb(x,y,z,R)*z/denom
    else:
        gradx=0.
        grady=0.
        gradz=0.
        
    return [gradx,grady,gradz]

In [9]:
def norm_molorb(R):
    import math
    from math import exp 
    from math import sqrt
    from math import pi

# this a fitting formula for the norm of the orbital
# to avoid to recalculate the (non-trivial) overlap integral
    afit=0.460515
    bfit=0.940009
    cfit=0.532886
    dfit=0.270818
    val=afit*math.exp(-bfit*R*R) + cfit*math.exp(-dfit*R*R)
    val=2.+2.*val
    val=1./math.sqrt(val)

    return val

In [10]:
def molecular_orb(x,y,z,R):
    val=norm_molorb(R)*(atomic_orbital(x,y,z,-R/2)+atomic_orbital(x,y,z,R/2))
    return val

In [11]:
def dens(x,y,z,R):
    val=molecular_orb(x,y,z,R)*molecular_orb(x,y,z,R)
    val=2.*val # we have 2 elecrons inside the orbital
    return val

In [12]:
def grad_dens(x,y,z,R):
    gradx=4.*molecular_orb(x,y,z,R)*(grad_atomic_orb(x,y,z,R/2)[0] \
                                     +grad_atomic_orb(x,y,z,-R/2)[0])
    grady=4.*molecular_orb(x,y,z,R)*(grad_atomic_orb(x,y,z,R/2)[1] \
                                     +grad_atomic_orb(x,y,z,-R/2)[1])
    gradz=4.*molecular_orb(x,y,z,R)*(grad_atomic_orb(x,y,z,R/2)[2] \
                                     +grad_atomic_orb(x,y,z,-R/2)[2])
    return [gradx,grady,gradz]

In [13]:
def abs_grad_dens(x,y,z,R):
    import math
    from math import sqrt
    # here we define the norm of the gradient |grad(rho(x,y,z)|
    gradx,grady,gradz=grad_dens(x,y,z,R)
    val=sqrt(gradx**2.+grady**2.+gradz**2.)
    return val

In [14]:
def s(x,y,z,R):    
    import math
    from math import sqrt
    # here we define the reduced gradient s(x,y,z) = |grad(rho(x,y,z))|/rho(x,y,z)^(4/3)
    val=abs_grad_dens(x,y,z,R)/dens(x,y,z,R)**(4./3.)
    return val

Now we have everything defined for plotting the NCI for 2 hydrogen atoms

In [ ]:
import sys
import numpy as np
import matplotlib.pyplot as plt

# we have to create table for a fixed R with triples (x,dens,s) for y,z=0

# in the plot we need x_table, s_table, rho_table for plotting 
# s aginst x, rho against x, and s against rho

R=5.5

# we plot from -2R to 2R in nmax+1 points
# dx = 4 R/(nmax)
# x0 = -2 R

nmax=500
dx=4*R/nmax
x0=-2.*R


# initialize the tables 
x_table=[]
rho_table=[]
s_table=[]
x=x0

# the loop
for i in range(nmax):
    x_table.append(x)
    s_table.a



# The plots    
fig, (ax1, ax2, ax3) = plt.subplots(1, 3,figsize=(18,6))
fig.suptitle('rho against x   --  s against x   --       s against rho')
ax1.plot(x_table, rho_table)
ax2.set_ylim(0,50)
ax2.plot(x_table,s_table)
ax3.set_ylim(0,50)
ax3.plot(rho_table,s_table)